Adapted from: https://docs.scipy.org/doc/scipy/reference/tutorial/optimize.html#global-optimization

In [ ]:
%matplotlib inline

import numpy as np
import matplotlib.pyplot as plt

from mpl_toolkits.mplot3d import Axes3D
from scipy import optimize
from scipy.optimize import OptimizeResult

In [ ]:
def egg_carton(x):
    return (-(x[1] + 47) * np.sin(np.sqrt(abs(x[0]/2 + (x[1]  + 47))))
            -x[0] * np.sin(np.sqrt(abs(x[0] - (x[1]  + 47)))))    

In [ ]:
def plot_egg_carton(bounds):
    x = np.arange(bounds[0][0], bounds[0][1])
    y = np.arange(bounds[1][0], bounds[1][1])
    
    xgrid, ygrid = np.meshgrid(x, y)
    xy = np.stack([xgrid, ygrid])

    fig = plt.figure(figsize=[10, 10])
    ax = fig.add_subplot(111, projection='3d')
    ax.view_init(45, -45)
    ax.plot_surface(xgrid, ygrid, egg_carton(xy), cmap='terrain')
    ax.set_xlabel('x')
    ax.set_ylabel('y')
    ax.set_zlabel('egg_carton(x, y)')
    
    plt.show()
    return xy

In [ ]:
bounds = [(-512, 512), (-512, 512)]

In [ ]:
xy = plot_egg_carton(bounds)

In [ ]:
def plot_heatmap(xy, bounds, results):
    
    def plot_point(result, marker='.', color=None, ms=1):
        ax.plot(bounds[0][1] + result.x[0], bounds[1][1] + result.x[1], 
                marker=marker, color=color, ms=ms)
    
    fig = plt.figure(figsize=[10, 10])
    ax  = fig.add_subplot(111)
    im  = ax.imshow(egg_carton(xy), interpolation='bilinear', origin='lower', cmap='gray')
    ax.set_xlabel('x')

    plot_point(results['BH'], color='yellow', marker='o', ms=10)  # basin hopping
    plot_point(results['DE'], color='cyan',   marker='o', ms=10)  # differential evolution
    plot_point(results['DA'], color='white',  marker='o', ms=10)  # dual annealing

    plot_point(results['shgo'],       color='red', marker='+', ms=10)
    plot_point(results['shgo_sobol'], color='red', marker='x', ms=10)

    # SHGO produces multiple minima, plot them all (with a smaller marker size)
    for i in range(results['shgo_sobol'].xl.shape[0]):
        res = OptimizeResult()
        res.x = np.array([results['shgo_sobol'].xl[i, 0], results['shgo_sobol'].xl[i, 1]])
        plot_point(res, color='red', marker='.', ms=8)

    ax.set_xlim([-4, 514*2])
    ax.set_ylim([-4, 514*2])

    plt.show()

In [ ]:
results = dict()

results['DA'] = optimize.dual_annealing(egg_carton, bounds)
results['DE'] = optimize.differential_evolution(egg_carton, bounds)
results['BH'] = optimize.basinhopping(egg_carton, bounds)

results['shgo']       = optimize.shgo(egg_carton, bounds)
results['shgo_sobol'] = optimize.shgo(egg_carton, bounds, n=200, iters=5,
                                      sampling_method='sobol')

In [ ]:
plot_heatmap(xy, bounds, results)